### A Data Warehouse on top of Delta lake using Spark
### Scientific Publications Dataset

Authors: Jose Rodrigo Flores Espinosa & Marta Napa  
email: rodrigo.flores@ut.ee & marta.napa@ut.ee

### Objective

- The purpose is to extract data about scientific publications from JSON data that describe a huge number of papers and populate a data warehouse in order to issue analytics queries using SQL.  
- We will use Spark DataFrames to extract and transform the data.  
- We will use also Spark tables (delta tables) to be used for dimensions and fact table

### Dataset

Data set The source of the data is [https://www.aminer.org/citation](https://www.aminer.org/citation), version 13 as it is the most detailed one in JSON format.

### Overview

- Load required libraries
- Download of JSON data into Databricks
- Pre-processing of JSON data
- ETL processing
- Data Warehouse building
  - Save into persistent Delta tables
- Data Warehouse querying

### Spark Session

In [0]:
from pyspark.conf import SparkConf
from pyspark.context import SparkContext

conf = SparkConf()
display(conf.getAll())

_1 _2 spark.executor.memory 8278m spark.ui.port 40001 spark.executor.extraClassPath /databricks/spark/dbconf/log4j/executor:/databricks/spark/dbconf/jets3t/:/databricks/spark/dbconf/hadoop:/databricks/hive/conf:/databricks/jars/----com_google_protobuf--timestamp_proto-spark_3.2_2.12-scalabp.jar:/databricks/jars/----glue-catalog-spark3.2-client--glue-catalog-client-common_deploy.jar:/databricks/jars/----glue-catalog-spark3.2-client--glue-catalog-hive2-client_deploy.jar:/databricks/jars/----glue-catalog-spark3.2-client--glue-catalog-shim-common_deploy.jar:/databricks/jars/----glue-catalog-spark3.2-client--glue-catalog-shim-hive1_deploy.jar:/databricks/jars/----glue-catalog-spark3.2-client--glue-catalog-shim-hive2_deploy.jar:/databricks/jars/----glue-catalog-spark3.2-client--glue-catalog-shim-loader_deploy.jar:/databricks/jars/----jackson_annotations_shaded--libjackson-annotations.jar:/databricks/jars/----jackson_core_shaded--libjackson-core.jar:/databricks/jars/----jackson_databind_shaded--libjackson-databind.jar:/databricks/jars/----jackson_datatype_joda_shaded--libjackson-datatype-joda.jar:/databricks/jars/----scalapb_090--com.lihaoyi__fastparse_2.12__2.1.3_shaded.jar:/databricks/jars/----scalapb_090--com.lihaoyi__sourcecode_2.12__0.1.7_shaded.jar:/databricks/jars/----scalapb_090--runtime-unshaded-jetty9-hadoop1_2.12_deploy_shaded.jar:/databricks/jars/----workspace_spark_3_2--common--kvstore--kvstore-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--common--network-common--network-common-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--common--network-shuffle--network-shuffle-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--common--sketch--sketch-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--common--tags--tags-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--common--unsafe--unsafe-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--core--core-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--core--libcore_generated_resources.jar:/databricks/jars/----workspace_spark_3_2--core--libcore_resources.jar:/databricks/jars/----workspace_spark_3_2--core--proto-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--graphx--graphx-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--launcher--launcher-hive-2.3__hadoop-3.2_2.12_deploy.jar:/databricks/jars/----workspace_spark_3_2--maven-trees--hive-2.3__hadoop-3.2--antlr--antlr--antlr__antlr__2.7.7.jar:/databricks/jars/----workspace_spark_3_2--maven-trees--hive-2.3__hadoop-3.2--com.amazonaws--amazon-kinesis-client--com.amazonaws__amazon-kinesis-client__1.12.0.jar:/databricks/jars/----workspace_spark_3_2--maven-trees--hive-2.3__hadoop-3.2--com.amazonaws--aws-java-sdk-autoscaling--com.amazonaws__aws-java-sdk-autoscaling__1.12.189.jar:/databricks/jars/----workspace_spark_3_2--maven-trees--hive-2.3__hadoop-3.2--com.amazonaws--aws-java-sdk-cloudformation--com.amazonaws__aws-java-sdk-cloudformation__1.12.189.jar:/databricks/jars/----workspace_spark_3_2--maven-trees--hive-2.3__hadoop-3.2--com.amazonaws--aws-java-sdk-cloudfront--com.amazonaws__aws-java-sdk-cloudfront__1.12.189.jar:/databricks/jars/----workspace_spark_3_2--maven-trees--hive-2.3__hadoop-3.2--com.amazonaws--aws-java-sdk-cloudhsm--com.amazonaws__aws-java-sdk-cloudhsm__1.12.189.jar:/databricks/jars/----workspace_spark_3_2--maven-trees--hive-2.3__hadoop-3.2--com.amazonaws--aws-java-sdk-cloudsearch--com.amazonaws__aws-java-sdk-cloudsearch__1.12.189.jar:/databricks/jars/----workspace_spark_3_2--maven-trees--hive-2.3__hadoop-3.2--com.amazonaws--aws-java-sdk-cloudtrail--com.amazonaws__aws-java-sdk-cloudtrail__1.12.189.jar:/databricks/jars/----workspace_spark_3_2--maven-trees--hive-2.3__hadoop-3.2--com.amazonaws--aws-java-sdk-cloudwatch--com.amazonaws__aws-java-sdk-cloudwatch__1.12.189.jar

#### Spark Configuration

In [0]:
# partitions
spark.conf.set("spark.sql.shuffle.partitions", sc.defaultParallelism) # reduce parallelism for aggregations and joins, set it to amount of cores. Faster processing
# spark.conf.set("spark.sql.shuffle.partitions", 2)

In [0]:
# spark.conf.get('spark.sql.files.maxPartitionBytes')
spark.conf.get('spark.sql.shuffle.partitions')


Out[3]: '8'

### Libraries

In [0]:
%sh 

# installing libraries
pip install py7zr unidecode --quiet --disable-pip-version-check


In [0]:
# libraries

import pyspark.sql.functions as F
from pyspark.sql.types import *

from IPython.display import Image 
from IPython.core.display import HTML 

import numpy as np
import pandas as pd

from string import ascii_letters, punctuation
from unidecode import unidecode
from urllib.request import urlopen
import urllib 
import json
import py7zr
import re
import os

### Data importing

- Downloading of main JSON zipped data (~2.4 Gb)  
- Decompression of JSON data (~17 Gb)  
- Fetching of manually curated data from [EGI Confluence](https://confluence.egi.eu/display/EGIG/Scientific+Disciplines) on normalized disciplines classification

In [0]:
%sh

ls -lh /mnt/

total 8.0K
drwxr-xr-x 2 root root 4.0K May 27 07:02 driver-daemon
drwxr-xr-x 2 root root 4.0K May 27 07:01 readonly


In [0]:
# local variables

local_path = '/mnt/'

In [0]:
# Retrieve the zip file
# https://docs.databricks.com/data/data-sources/zip-files.html
file_url = 'https://originalstatic.aminer.cn/misc/dblp.v13.7z'
file = local_path + 'dblp.v13.7z'

print("Downloading file from source")
urllib.request.urlretrieve(file_url, file)

# Unzip compressed file  
print("Unzipping 7z file")
archive = py7zr.SevenZipFile(file, mode='r')
archive.extractall(path=local_path)
archive.close()

Unzipping 7z file


In [0]:
%sh 

echo 'Deleting zipped JSON file'
rm /mnt/dblp.v13.7z


Deleting zipped JSON file


In [0]:
%sh

echo 'Fetching 'field of study' (fos) data'
wget --quiet -P /mnt https://raw.githubusercontent.com/JRodrigoF/bdm_g6/main/p1/data/dictionary_fos.txt

ls -lsh /mnt/

Fetching field of study (fos) data
total 32K
 24K -rw-r--r-- 1 root root  21K Jun 10 07:05 dictionary_fos.txt
4.0K drwxr-xr-x 2 root root 4.0K Jun 10 07:02 driver-daemon
4.0K drwxr-xr-x 2 root root 4.0K Jun 10 07:02 readonly


In [0]:
%sh

head -50 /mnt/dictionary_fos.txt

[
{

		"mathematics" : "natural sciences",
		"computer sciences" : "natural sciences",
		"information sciences" : "natural sciences",
		"earth sciences" : "natural sciences",
		"biology science" : "natural sciences",
		"physical sciences" : "natural sciences",
		"chemical sciences" : "natural sciences",

		"civil engineering" : "engineering and technology",
		"electrical, electronic and information engineering" : "engineering and technology",
		"mechanical engineering" : "engineering and technology",
		"aerospace engineering" : "engineering and technology",
		"chemical engineering" : "engineering and technology",
		"materials engineering" : "engineering and technology",
		"bioengineering and biomedical engineering" : "engineering and technology",
		"environmental engineering" : "engineering and technology",
		"environmental biotechnology" : "engineering and technology",
		"industrial biotechnology" : "engineering and technology",
		"nano-technology" : "engineering and technology",
		"n

### Data pre-processing

- Parsing of JSON file
  - Making JSON data format-conforming
    - Fixing of 'string' fields into integer
  - Splitting file into chunks/parts with 250K entries each
  - Output gets stored in the local file system (/mnt/)

In [0]:
input_file = local_path + 'dblpv13.json'
output_file = local_path + 'dblpv13_edited_part_1.json'

out = open(output_file, 'w')
n_elements = 250000
counter = 0
file = 1
entries = 0

print('Processing JSON data')
print('Writing compliant JSON file part {}'.format(file))
with open(input_file, 'r') as f:
    for line in f:
        if 'NumberInt' in line:
            line = line.replace("NumberInt(", "").replace(")", "")
            out.write(line)
        else:
            if re.match('^},', line):
                counter += 1
                entries += 1
                if counter == n_elements:
                    out.write('}]')
                    out.close()
                    file += 1
                    print('Writing compliant JSON file part {}'.format(file))
                    output_file = local_path + 'dblpv13_edited_part_{}.json'.format(file)
                    out = open(output_file, 'w')
                    out.write('[')
                    counter = 0
                else:
                    out.write(line)
            else:
                out.write(line)
    out.close()

print('{} entries processed'.format(entries))
            

Processing JSON data
Writing compliant JSON file part 1
Writing compliant JSON file part 2
Writing compliant JSON file part 3
Writing compliant JSON file part 4
Writing compliant JSON file part 5
Writing compliant JSON file part 6
Writing compliant JSON file part 7
Writing compliant JSON file part 8
Writing compliant JSON file part 9
Writing compliant JSON file part 10
Writing compliant JSON file part 11
Writing compliant JSON file part 12
Writing compliant JSON file part 13
Writing compliant JSON file part 14
Writing compliant JSON file part 15
Writing compliant JSON file part 16
Writing compliant JSON file part 17
Writing compliant JSON file part 18
Writing compliant JSON file part 19
Writing compliant JSON file part 20
Writing compliant JSON file part 21
Writing compliant JSON file part 22
5354308 entries processed


In [0]:
%sh

echo 'Deleting JSON single file'
rm /mnt/dblpv13.json

ls -lsh /mnt/

Deleting JSON single file
total 16G
655M -rw-r--r-- 1 root root 655M Jun  8 08:29 dblpv13_edited_part_1.json
751M -rw-r--r-- 1 root root 751M Jun  8 08:34 dblpv13_edited_part_10.json
759M -rw-r--r-- 1 root root 759M Jun  8 08:35 dblpv13_edited_part_11.json
813M -rw-r--r-- 1 root root 813M Jun  8 08:35 dblpv13_edited_part_12.json
679M -rw-r--r-- 1 root root 679M Jun  8 08:36 dblpv13_edited_part_13.json
717M -rw-r--r-- 1 root root 717M Jun  8 08:36 dblpv13_edited_part_14.json
706M -rw-r--r-- 1 root root 706M Jun  8 08:36 dblpv13_edited_part_15.json
798M -rw-r--r-- 1 root root 798M Jun  8 08:37 dblpv13_edited_part_16.json
818M -rw-r--r-- 1 root root 818M Jun  8 08:37 dblpv13_edited_part_17.json
837M -rw-r--r-- 1 root root 837M Jun  8 08:38 dblpv13_edited_part_18.json
818M -rw-r--r-- 1 root root 818M Jun  8 08:38 dblpv13_edited_part_19.json
734M -rw-r--r-- 1 root root 734M Jun  8 08:30 dblpv13_edited_part_2.json
804M -rw-r--r-- 1 root root 804M Jun  8 08:39 dblpv13_edited_part_20.json
747M

### Data Extraction & Transformation

- Reading of 'field of study' (fos) data into two dictionaries
  - general fos
  - specific fos
- ETL functions    
- Schema specification
  - To be used for storing/reading data as Delta tables
- ETL processing  
  (Performed iteratively on each JSON part)  

  - Entries are discarded if:
    - title is empty or consist of only one word
    - "foreword", "editor" or "book" appears in the title 
    - if the title is contained in a pre-defined "blacklist" ("[review article]", "In this issue", "about the cover", ..)  
    - if the number of citations in the entry is 0 or not present 
  - Authors / organizations
    - entries with no authors listed are removed
    - authors present in a pre-defined "blacklist" ("anonymous", "NA", "dr.", ..) of non-valid authors are removed from the entry
    - author names are cleaned for any extra punctuation symbols both at the begging and at the end of the string
    - author organizations are cleaned for any extra punctuation symbols both at the begging and at the end of the string
  - DOI
    - entries are searched for a valid DOI pattern, if not matched, "NA" gets assigned
    - string 'https://doi.org/' is removed from the DOI string
  - ISSN
    - if ISSN is not present in the entry, an attempt is made to obtain it from the DOI, which is cleaned first
    - entries are matched to the pattern they should have and in case of mismatch "NA" is assigned
  - ISBN
    - entries are matched to the pattern and length they should have, which is not unique but more than one posibility exist. In case of mismatch "NA" is assigned
  - Abstract
    - entries are cleaned for any extra punctuation symbols or non-informative strings both at the begging and at the end of the string
  - Venue
    - Only fields "name", "type", "raw" are retained
    - Fields are cleaned for extra punctuation symbols both at the begging and at the end of the string
    - Using a combination of 1) text search based on venue fields "name" and "raw", 2) text searches in the cleaned field "abstract" from the main entry, 3) presence of valid ISBN and heuristics (e.g. venues where an acronym is given), the following document categories are determined
      - journal
      - book
      - conference
      - workshop
      - seminar
      - colloquium
      - symposium
      - unknown
  - Year
    - field is retained. Non-integer entries are turned to "NA"
  - Volume
    - values are cleaned for any ascii characters before isistance(int) is applied
  - Language
    - entries are kept. If not present or empty then "NA" is recorded
  - Field of Study
    - Two categories have been curated from [EGI Confluence](https://confluence.egi.eu/display/EGIG/Scientific+Disciplines) on normalized disciplines classifications
      - general
      - specific
    - curation involved spliting many composed unormalized terms into simpler versions more likely to be found as such. For example:  
      "electrical and electronic engineering" becomes
        "electrical engineering"  
        "electronic engineering"
    
    - all unormalized fos categories are match against the curated fos hash tables and if a specific category finds a hit, a second more general categroy defined is also recorded
  - Keywords
    - entries are cleaned for any extra punctuation symbols or non-informative strings both at the begging and at the end of the string

- Resulting Spark DataFrames are stored persistently as Delta tables in DBFS
  - One for each JSON part

#### Extraction & Transformation functions

In [0]:
input_file = local_path + "dictionary_fos.txt"

with open(input_file) as f:
    dict_fos = f.read()
    dict_fos = json.loads(dict_fos)

dict_fos_discipline = dict_fos[0]
dict_fos_subdiscipline = dict_fos[1]

In [0]:
# parsing functions for raw dict entries

def doi2issn(doi):
    if '/' in doi:
        issn = doi.split('/')[1].split('(')[0]
        if re.match("[0-9]{4}-[0-9]{3}[X0-9]", issn):
            return issn
        else:
            return 'NA'
    else:
        return 'NA'

def parse_issn(issn, paper):
    issn = paper['issn'].split(' ')[0]
    if re.match("[0-9]{4}-[0-9]{3}[X0-9]", issn):
        return issn
    else:
        return 'NA'

def words_in_string(word_list, a_string):
    return set(word_list).intersection(a_string.split())

# https://stackoverflow.com/questions/11150239/natural-sorting
def natural_sort(l): 
    convert = lambda text: int(text) if text.isdigit() else text.lower() 
    alphanum_key = lambda key: [convert(c) for c in re.split('([0-9]+)', key)] 
    return sorted(l, key=alphanum_key)

title_blacklist = {
    '[review article]':-1,
    'In the news':-1,
    '(no title)':-1,
    'In this issue …':-1,
    '[title page]':-1,
    '[without title]':-1,
    'about the cover':-1,
    'about the issue':-1,
    'about the proceedings':-1,
    'about the authors':-1,
    'about this journal':-1,
    }

keyword_blacklist = {'03-03':-1,
                     '! !"! ! !###! ! !! ! "':-1}
    
def etl_processing(dict_entry, title_blacklist=title_blacklist, keyword_blacklist=keyword_blacklist):
    
    paper = dict_entry
            
    # Title
    if 'title' not in paper or paper['title'] == "" or paper['title'] == None or paper['title'] == 'None':
        return None
    
    title = paper['title'].strip('.: ').lower()
    if len(title.split(' ')) == 1:
        return None
        
    if 'foreword' in title or 'editor' in title or 'book' in title or title in title_blacklist:
        return None

    if 'n_citation' not in paper or paper['n_citation'] == 0:
        return None
    
    clean_paper = {}
    clean_paper['id'] = paper['_id']
    clean_paper['title'] = paper['title'].strip('.: ')
    clean_paper['n_citation'] = paper['n_citation']

    # authors & organization
    if 'authors' not in paper or paper['authors'] == []:
        return None
    
    authors_blacklist = ['staff', 'ieee', 'anonymous', 'NA', 'dr.', '']
    authors = [] 
    
    for author in paper['authors']:
        
        clean_author = {
            'name': 'NA',
            'org': 'NA'
        }
        
        if 'name' in author and author['name'] != '' and not words_in_string(authors_blacklist, author['name'].lower()):
            clean_author['name'] = author['name'].strip('.:,-&/ ')
        else:
            continue
            
        if 'org' in author and author['org'] != '' and author['org'] not in 'Corresponding author':
            clean_author['org'] = author['org'].strip('(Correspd.:,-&/)#N*<i> ')
            
        authors.append(clean_author) 
    
    if authors == []:
        return None
    else:
        clean_paper['authors'] = authors      
        
    # issn
    if 'issn' not in paper and 'doi' in paper:
        clean_paper['issn'] = doi2issn(paper['doi'])
    elif 'issn' not in paper and 'doi' not in paper:
        clean_paper['issn'] = 'NA'
    elif 'issn' in paper and 'doi' in paper:
        issn = parse_issn(paper['issn'], paper)
        if issn == 'NA':
            clean_paper['issn'] = doi2issn(paper['doi'])
        else:
            clean_paper['issn'] = issn
    else:
        clean_paper['issn'] = parse_issn(paper['issn'], paper)

    # doi
    if 'doi' not in paper:
        clean_paper['doi'] = 'NA'
    else:
        if '/' in paper['doi']:
            doi = paper['doi'].strip('https://doi.org/')
            if re.match("10.[0-9]{4}", doi):
                clean_paper['doi'] = doi
            else:
                clean_paper['doi'] = 'NA'
        else:
            clean_paper['doi'] = 'NA'
            
    # isbn
    if 'isbn' not in paper or paper['isbn'] == '' or paper['isbn'] == 'isbn':
        clean_paper['isbn'] = 'NA'
    else:
        isbn = paper['isbn']
#         if re.match("[0-9]{3}-[0-9]{1}-[0-9]{4}-[0-9]{4}-[0-9X]{1}", isbn):
#             clean_paper['isbn'] = isbn
        str_ = re.sub('-', '', isbn)
        if len(str_) == 10 or len(str_) == 13 or len(str_) == 9:
            clean_paper['isbn'] = isbn
        elif re.match("[0-9]{9}[0-9X]{1}", isbn):
            clean_paper['isbn'] = '{}-{}-{}-{}'.format(isbn[0],isbn[1:6],isbn[6:9],isbn[9])
        elif re.match("[0-9]{13}", isbn):
            clean_paper['isbn'] = '{}-{}-{}-{}-{}'.format(n[0:3],n[3],n[4:8],n[8:12],n[12])
        else:
            clean_paper['isbn'] = 'NA'

    # type of publication
    # pre-checks and captures abstract field
    abstract = 'NA'
    if 'abstract' in paper and paper['abstract'] != '' and paper['abstract'] != 'Without Abstract':
         abstract = paper['abstract'].strip(punctuation).strip()
    
    # venue
    venue_dict = {
        'name': 'NA',
        'type': 'NA',
        'raw': 'NA'
    }

    if 'venue' in paper:
        if 'raw' in paper['venue'] and paper['venue']['raw'] != None:
            venue_dict['raw'] =  paper['venue']['raw'].rstrip('.:()01234567890 ')
        if 'name_d' in paper['venue'] and paper['venue']['name_d'] != None:
            venue_dict['name'] = paper['venue']['name_d'].rstrip('.: ')
        if 'type' in paper['venue'] and paper['venue']['type'] != None:
            venue_dict['type'] = int(str(paper['venue']['type']).rstrip('.: '))
    
    clean_paper['venue'] = venue_dict
    
    VENUE = venue_dict['raw'] + ' ' + venue_dict['name']
    venue = VENUE.lower()
    
    # Journal case
    if 'journal' in venue or 'trans' in venue or 'ann' in venue or 'review' in venue or 'j.' in venue:
        doc_type = 'journal'
    elif 'this paper' in abstract.lower():
        doc_type = 'journal'
    # Book case
    elif clean_paper['isbn'] != 'NA':
        doc_type = 'book'
    # Conference case
    elif venue_dict['raw'] != 'NA' and venue_dict['raw'].isupper(): 
        doc_type = 'conference'
    elif 'conference' in venue or 'IEEE' in VENUE or 'congress' in venue:
        doc_type = 'conference'
    # Workshop case
    elif 'workshop' in venue:
        doc_type = 'workshop'
    # Seminar case
    elif 'seminar' in venue:
        doc_type = 'seminar'
    # Colloquium case
    elif 'colloquium' in venue:
        doc_type = 'colloquium'
    # Symposium case
    elif 'symposium' in venue:
        doc_type = 'symposium'
    else:
        doc_type = 'unknown'
    
    clean_paper['doc_type'] = doc_type
                
    # year
    clean_paper['year'] = 'NA'
    if 'year' in paper and paper['year'] != '0':
        clean_paper['year'] = paper['year']
        
    # volume        
    clean_paper['volume'] = 'NA'
    if 'volume' in paper and paper['volume'] != '':
        volume = paper['volume'].strip('.:-&/ ' + ascii_letters)
        if isinstance(volume, int):
            clean_paper['volume'] = paper['volume']

    # language
    clean_paper['lang'] = 'NA'
    if 'lang' in paper and paper['lang'] != '':
        clean_paper['lang'] = paper['lang']
    
    # field of study (fos)
    clean_paper['fos_general'] = 'NA'
    clean_paper['fos_specific'] = 'NA'
    if 'fos' in paper and paper['fos'] != []:
        for fos in paper['fos']:
            fos = fos.lower()
            if fos.lower() in dict_fos_subdiscipline:
                clean_paper['fos_specific'] = dict_fos_subdiscipline[fos]
                clean_paper['fos_general'] = dict_fos_discipline[clean_paper['fos_specific']]
                break
            elif fos in dict_fos_discipline:
                clean_paper['fos_general'] = dict_fos_discipline[fos]
                break           
                    
    # keywords
    clean_paper['keywords'] = ['NA']
    clean_keywords = []
    if 'keywords' in paper and paper['keywords'] != []:
        for keyword in paper['keywords']:
            keyword = keyword.strip('.- ').lower()

            if re.match('[0-9]{2}[a-z]+[0-9]{2}$', keyword):
                continue
            elif re.match('[0-9]{2} [a-z]+ [0-9]{2}$', keyword):
                continue
            elif re.match('[a-z]{1}[0-9]{2}$', keyword):
                continue
            elif re.match('[0-9]{2}\.[0-9]{2}\.[a-z]{2}$', keyword):
                continue
            elif re.match('[0-9]+\.[0-9]{2}\..*$', keyword):
                continue
            elif keyword in keyword_blacklist:
                continue
            elif isinstance(keyword, int):
                continue
            elif re.match('[0-9]+$', keyword):
                continue
            elif keyword == '':
                continue
            else:
                clean_keywords.append(keyword.lower())
                
        if clean_keywords != []:
            clean_paper['keywords'] = clean_keywords
        
    # abstract
    clean_paper['abstract'] = abstract
        
    return clean_paper

#### dblpv13 schema

In [0]:
Image(url= "https://raw.githubusercontent.com/JRodrigoF/bdm_g6/main/p1/data/dw_schema.png")

In [0]:
dblpv13_schema = (StructType()
                      .add("id", StringType(), False)
                      .add("title", StringType(), False)
                      .add("authors", ArrayType(
                                      StructType()
                                          .add("name", StringType(), True)
                                          .add("org", StringType(), True)
                                      ,False
                                      )
                          )
                      .add("doc_type", StringType(), True)
                      .add("n_citation", IntegerType(), True)
                      .add("issn", StringType(), True)
                      .add("isbn", StringType(), True)
                      .add("doi", StringType(), True)
                      .add("volume", StringType(), True)
                      .add("year", IntegerType(), True)
                      .add("venue", StructType()
                                      .add("name", StringType(), True)
                                      .add("type", StringType(), True)
                                      .add("raw", StringType(), True)
                          )
                      .add("lang", StringType(), True)
                      .add("fos_general", StringType(), True)
                      .add("fos_specific", StringType(), True)
                      .add("keywords", ArrayType(
                                           StringType(), True
                                       ), True
                          )
                      .add("abstract", StringType(), True)
                 )


#### JSON to Delta tables

In [0]:
# ETL processing on each JSON part and storage of the resulting new JSOn data in DBFS

json_files = natural_sort([f for f in os.listdir(local_path) if f.startswith('dblpv13_edited_part_')])

for file in json_files:
    
    input_file = local_path + file
    output_file = input_file.replace('edited_part_', 'edited_parsed_part_')
    table_name = output_file.replace('.json', '').replace(local_path, '')
    
    print("Loading JSON file {}".format(input_file))
    f = open(input_file)
    data = json.load(f)
    f.close()
    parsed_dict = []

    print("---- Parsing file {}".format(input_file))
    for dict_entry in data:
        clean_entry = etl_processing(dict_entry)
        if clean_entry != None:
            parsed_dict.append(clean_entry)
    
    print("---- Writing file {}".format(output_file))
    with open(output_file, 'w', encoding='utf-8') as out:
           json.dump(parsed_dict, out)
        
    print("---- Writing delta table {}".format(table_name))
    dblpv13_df = spark.read.schema(dblpv13_schema).json("file:{}".format(output_file))
    dblpv13_df.write.format("delta").saveAsTable(table_name, mode='overwrite')
    
    print("---- Deleting (!) JSON files")
    os.remove(input_file)
    os.remove(output_file)


Loading JSON file /mnt/dblpv13_edited_part_1.json
---- Parsing file /mnt/dblpv13_edited_part_1.json
---- Writing file /mnt/dblpv13_edited_parsed_part_1.json
---- Writing delta table dblpv13_edited_parsed_part_1
---- Deleting (!) JSON files
Loading JSON file /mnt/dblpv13_edited_part_2.json
---- Parsing file /mnt/dblpv13_edited_part_2.json
---- Writing file /mnt/dblpv13_edited_parsed_part_2.json
---- Writing delta table dblpv13_edited_parsed_part_2
---- Deleting (!) JSON files
Loading JSON file /mnt/dblpv13_edited_part_3.json
---- Parsing file /mnt/dblpv13_edited_part_3.json
---- Writing file /mnt/dblpv13_edited_parsed_part_3.json
---- Writing delta table dblpv13_edited_parsed_part_3
---- Deleting (!) JSON files
Loading JSON file /mnt/dblpv13_edited_part_4.json
---- Parsing file /mnt/dblpv13_edited_part_4.json
---- Writing file /mnt/dblpv13_edited_parsed_part_4.json
---- Writing delta table dblpv13_edited_parsed_part_4
---- Deleting (!) JSON files
Loading JSON file /mnt/dblpv13_edited_pa

In [0]:
%fs

ls /user/hive/warehouse/dblpv13_edited_parsed_part_1/

path name size modificationTime dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_1/_SUCCESS _SUCCESS 0 1653637259000 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_1/_committed_8058540948611346725 _committed_8058540948611346725 122 1653637258000 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_1/_started_8058540948611346725 _started_8058540948611346725 0 1653637235000 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_1/part-00000-tid-8058540948611346725-1a6da28f-d011-4bb9-a266-30ae3d369f2a-0-1-c000.snappy.parquet part-00000-tid-8058540948611346725-1a6da28f-d011-4bb9-a266-30ae3d369f2a-0-1-c000.snappy.parquet 116165071 1653637255000

In [0]:
display(spark.sql("SELECT * FROM {}.`{}`".format(table_format, dblpv13_delta_parts[0])))

id title authors doc_type n_citation issn isbn doi volume year venue lang fos_general fos_specific keywords abstract 53e99784b7602d9701f3e151 A solution to the problem of touching and broken characters List(List(Jairo Rocha, NA), List(Theo Pavlidis, NA)) conference 17 NA NA 10.1109/ICDAR.1993.395663 NA 1993 List(International Conference on Document Analysis and Recognition, 0, ICDAR-) en natural sciences computer sciences List(handwriting recognition, prototypes, image segmentation, computer science, expert systems, knowledge base, pattern recognition, usability, optical character recognition, shape, feature extraction) NA 53e99784b7602d9701f3e15d Timing yield estimation using statistical static timing analysis List(List(Min Pan, NA), List(Chris C. N. Chu, NA), List(Hai Zhou, NA)) book 28 NA 0-7803-8834-8 10.1109/ISCAS.2005.1465124 NA 2005 List(International Symposium on Circuits and Systems, 0, ISCAS) en NA NA List(sequential circuits, statistical distributions, set-up time constraints, register-to-register paths, statistical static timing analysis, integrated circuit modelling, parameter estimation, statistical analysis, circuit model, path delays, deep sub-micron technology, timing, delay distributions, delays, circuit timing, shortest path variations, hold time constraints, integrated circuit yield, process variations, integrated circuit layout, high-performance circuit designs, clock skew, timing yield estimation, deterministic static timing analysis, monte carlo simulation, design method, static timing analysis, design methodology, process variation, shortest path, registers, circuit design, circuit analysis) As process variations become a significant problem in deep sub-micron technology, a shift from deterministic static timing analysis to statistical static timing analysis for high-performance circuit designs could reduce the excessive conservatism that is built into current timing design methods. We address the timing yield problem for sequential circuits and propose a statistical approach to handle it. We consider the spatial and path reconvergence correlations between path delays, set-up time and hold time constraints, and clock skew due to process variations. We propose a method to get the timing yield based on the delay distributions of register-to-register paths in the circuit On average, the timing yield results obtained by our approach have average errors of less than 1.0% in comparison with Monte Carlo simulation. Experimental results show that shortest path variations and clock skew due to process variations have considerable impact on circuit timing, which could bias the timing yield results. In addition, the correlation between longest and shortest path delays is not significant 53e99784b7602d9701f3e922 International Conference on Nano/Micro Engineered and Molecular Systems List(List(Jungil Park, NA), List(Sunyoung Ahn, NA), List(Youngmi Kim Pak, NA), List(James Jungho Pak, NA)) conference 1 NA NA 10.1109/NEMS.2009.5068754 NA 2009 List(NA, NA, NEMS) en NA NA List(NA) NA 53e99784b7602d9701f3f411 Using XML to Integrate Existing Software Systems into the Web List(List(Harry M. Sneed, NA)) book 28 NA 0-7695-1727-7 10.1109/CMPSAC.2002.1044548 NA 2002 List(Computer Software and Applications Conference, 0, COMPSAC) en natural sciences computer sciences List(internet, hypermedia markup languages, information resources, systems re-engineering, cobol, pl/i, world wide web, xml, batch programs, data conversion, e-commerce, extensible markup language, enterprise application integration, interface reengineering, legacy programs, online programs, software reengineering, subprograms, systems integration) The eXtensible Markup Language 驴 XML 驴 is not only a language for communication between humans and the web, it is also a language for communication between programs. Rather than passing parameters, programs can pass documents from one to another, containing not only pure data, but control information as well. Even legacy

### Data Warehouse

- Reading and joining of all persisted Delta tables (120 Mb each) into a single one
- Schema definition for dimension and fact tables
  - Intended for faster reading of data from persisted Delta tables
  - \#todo add schema option to spark.sql.read
- Building and storage (Delta tables) of dimension tables
- Building and storage (Delta tables) of fact table

In [0]:
%sh

ls -lh /mnt/

total 8.0K
drwxr-xr-x 2 root root 4.0K Jun  6 19:21 driver-daemon
drwxr-xr-x 2 root root 4.0K Jun  6 19:21 readonly


#### Joining Delta Tables

In [0]:
%sh

ls /dbfs

In [0]:
# fetches all delta table file names/paths present in DBFS

d = dbutils.fs.ls("/user/hive/warehouse/")
dblpv13_delta_parts = []

for l in d:
    file = str(l).split()[0]
    if 'dblpv13_edited_parsed_part' in file:
        dblpv13_delta_parts.append((file.replace("FileInfo(path='dbfs:", "").replace("/',", "")))

dblpv13_delta_parts = (natural_sort(dblpv13_delta_parts))
print("There are {} Delta tables present at /user/hive/warehouse/\n".format(len(dblpv13_delta_parts)))
print(dblpv13_delta_parts)


There are 22 Delta tables present at /user/hive/warehouse/

['/user/hive/warehouse/dblpv13_edited_parsed_part_1', '/user/hive/warehouse/dblpv13_edited_parsed_part_2', '/user/hive/warehouse/dblpv13_edited_parsed_part_3', '/user/hive/warehouse/dblpv13_edited_parsed_part_4', '/user/hive/warehouse/dblpv13_edited_parsed_part_5', '/user/hive/warehouse/dblpv13_edited_parsed_part_6', '/user/hive/warehouse/dblpv13_edited_parsed_part_7', '/user/hive/warehouse/dblpv13_edited_parsed_part_8', '/user/hive/warehouse/dblpv13_edited_parsed_part_9', '/user/hive/warehouse/dblpv13_edited_parsed_part_10', '/user/hive/warehouse/dblpv13_edited_parsed_part_11', '/user/hive/warehouse/dblpv13_edited_parsed_part_12', '/user/hive/warehouse/dblpv13_edited_parsed_part_13', '/user/hive/warehouse/dblpv13_edited_parsed_part_14', '/user/hive/warehouse/dblpv13_edited_parsed_part_15', '/user/hive/warehouse/dblpv13_edited_parsed_part_16', '/user/hive/warehouse/dblpv13_edited_parsed_part_17', '/user/hive/warehouse/dblpv13_

In [0]:
# function to concatenate delta tables in the form of Spark dataframes

def delta_concat(df_tgt, src_table_file, table_format):
    tmp_tbl = spark.sql("SELECT * FROM {}.`{}`".format(table_format, src_table_file))
    df_tgt = df_tgt.union(tmp_tbl)
    del tmp_tbl
    return df_tgt


In [0]:
# seeding table

# table_format="parquet"
table_format="delta"

df = spark.sql("SELECT * FROM {}.`{}`".format(table_format, dblpv13_delta_parts[0]))


In [0]:
# table_format="parquet"
table_format="delta"

for src_table_file in dblpv13_delta_parts[1:]:
    df = delta_concat(df, src_table_file, table_format)


In [0]:
display(df)
print("Number of total rows in the combined new Delta table:")
display(f"{df.count():,}") 
display(df.printSchema())


id title authors doc_type n_citation issn isbn doi volume year venue lang fos_general fos_specific keywords abstract 53e99784b7602d9701f3e151 A solution to the problem of touching and broken characters List(List(Jairo Rocha, NA), List(Theo Pavlidis, NA)) conference 17 NA NA 10.1109/ICDAR.1993.395663 NA 1993 List(International Conference on Document Analysis and Recognition, 0, ICDAR-) en natural sciences computer sciences List(handwriting recognition, prototypes, image segmentation, computer science, expert systems, knowledge base, pattern recognition, usability, optical character recognition, shape, feature extraction) NA 53e99784b7602d9701f3e15d Timing yield estimation using statistical static timing analysis List(List(Min Pan, NA), List(Chris C. N. Chu, NA), List(Hai Zhou, NA)) book 28 NA 0-7803-8834-8 10.1109/ISCAS.2005.1465124 NA 2005 List(International Symposium on Circuits and Systems, 0, ISCAS) en NA NA List(sequential circuits, statistical distributions, set-up time constraints, register-to-register paths, statistical static timing analysis, integrated circuit modelling, parameter estimation, statistical analysis, circuit model, path delays, deep sub-micron technology, timing, delay distributions, delays, circuit timing, shortest path variations, hold time constraints, integrated circuit yield, process variations, integrated circuit layout, high-performance circuit designs, clock skew, timing yield estimation, deterministic static timing analysis, monte carlo simulation, design method, static timing analysis, design methodology, process variation, shortest path, registers, circuit design, circuit analysis) As process variations become a significant problem in deep sub-micron technology, a shift from deterministic static timing analysis to statistical static timing analysis for high-performance circuit designs could reduce the excessive conservatism that is built into current timing design methods. We address the timing yield problem for sequential circuits and propose a statistical approach to handle it. We consider the spatial and path reconvergence correlations between path delays, set-up time and hold time constraints, and clock skew due to process variations. We propose a method to get the timing yield based on the delay distributions of register-to-register paths in the circuit On average, the timing yield results obtained by our approach have average errors of less than 1.0% in comparison with Monte Carlo simulation. Experimental results show that shortest path variations and clock skew due to process variations have considerable impact on circuit timing, which could bias the timing yield results. In addition, the correlation between longest and shortest path delays is not significant 53e99784b7602d9701f3e922 International Conference on Nano/Micro Engineered and Molecular Systems List(List(Jungil Park, NA), List(Sunyoung Ahn, NA), List(Youngmi Kim Pak, NA), List(James Jungho Pak, NA)) conference 1 NA NA 10.1109/NEMS.2009.5068754 NA 2009 List(NA, NA, NEMS) en NA NA List(NA) NA 53e99784b7602d9701f3f411 Using XML to Integrate Existing Software Systems into the Web List(List(Harry M. Sneed, NA)) book 28 NA 0-7695-1727-7 10.1109/CMPSAC.2002.1044548 NA 2002 List(Computer Software and Applications Conference, 0, COMPSAC) en natural sciences computer sciences List(internet, hypermedia markup languages, information resources, systems re-engineering, cobol, pl/i, world wide web, xml, batch programs, data conversion, e-commerce, extensible markup language, enterprise application integration, interface reengineering, legacy programs, online programs, software reengineering, subprograms, systems integration) The eXtensible Markup Language 驴 XML 驴 is not only a language for communication between humans and the web, it is also a language for communication between programs. Rather than passing parameters, programs can pass documents from one to another, containing not only pure data, but control information as well. Even legacy

Number of total rows in the combined new Delta table:
'3,412,291'root
 |-- id: string (nullable = true)
 |-- title: string (nullable = true)
 |-- authors: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- name: string (nullable = true)
 |    |    |-- org: string (nullable = true)
 |-- doc_type: string (nullable = true)
 |-- n_citation: integer (nullable = true)
 |-- issn: string (nullable = true)
 |-- isbn: string (nullable = true)
 |-- doi: string (nullable = true)
 |-- volume: string (nullable = true)
 |-- year: integer (nullable = true)
 |-- venue: struct (nullable = true)
 |    |-- name: string (nullable = true)
 |    |-- type: string (nullable = true)
 |    |-- raw: string (nullable = true)
 |-- lang: string (nullable = true)
 |-- fos_general: string (nullable = true)
 |-- fos_specific: string (nullable = true)
 |-- keywords: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- abstract: string (nullable = true)



#### DWH schema definition

In [0]:
from pyspark.sql.types import *

#### Dimension tables

# dim date
date_sc = StructType([
    StructField("id", IntegerType(), False),
    StructField("year", IntegerType(), False)
  ])

# dim document type
document_type_sc = StructType([
    StructField("id", IntegerType(), False),
    StructField("text", StringType(), False)
  ])

# dim publication
publication_sc = StructType([
    StructField("id", IntegerType(), False),
    StructField("title", StringType(), False),
    StructField("volume", StringType(), False),
    StructField("issn", StringType(), False),
    StructField("isbn", StringType(), False),
    StructField("doi", StringType(), False),
    StructField("n_citations", IntegerType(), False)
  ])

# dim venue
venue_sc = StructType([
    StructField("id", IntegerType(), False),
    StructField("name", StringType(), False)
  ])

# dim field of study (fos) general
fos_general_sc = StructType([
    StructField("id", IntegerType(), False),
    StructField("category", StringType(), False)
  ])

# dim field of study (fos) specific
fos_specific_sc = StructType([
    StructField("id", IntegerType(), False),
    StructField("category", StringType(), False)
  ])

# dim organization
organization_sc = StructType([
    StructField("id", IntegerType(), False),
    StructField("name", StringType(), False)
  ])

# dim author
author_sc = StructType([
    StructField("id", IntegerType(), False),
    StructField("firstname", StringType(), False),
    StructField("lastname", StringType(), False)
  ])

# dim language
language_sc = StructType([
    StructField("id", IntegerType(), False),
    StructField("text", StringType(), False)
  ])

#### Fact table

dblpFactTable_schema = StructType([
    StructField("date_id", IntegerType(), True), 
    StructField("doc_type_id", IntegerType(), True),
    StructField("publication_id", IntegerType(), True),
    StructField("venue_id", IntegerType(), True),
    StructField("fos_general_id", IntegerType(), True),
    StructField("fos_specific_id", IntegerType(), True),
    StructField("org_id", IntegerType(), True),
    StructField("author_id", IntegerType(), True),
    StructField("author_rank", IntegerType(), True)
  ])

#### Dimension tables

In [0]:
# dim date
(df
    .select(F.col("year"))
    .distinct()
    .sort("year")
    .withColumn("id", F.monotonically_increasing_id()+1)
    .selectExpr("id", "year")
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("dim_date")
)

# dim doc type
(df
    .selectExpr("doc_type")
    .dropDuplicates(["doc_type"])
    .withColumn("id", F.monotonically_increasing_id()+1)
    .selectExpr("id", "doc_type")
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("dim_doc_type")
)

# dim publication
(df
    .selectExpr("title", "volume", "issn", "isbn", "doi", "n_citation")
    .dropDuplicates(["title"])
    .withColumn("id", F.monotonically_increasing_id()+1)
    .selectExpr("id", "title", "volume", "issn", "isbn", "doi", "n_citation")
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("dim_publication")
)

# dim venue
(df
    .selectExpr("venue.name", "venue.raw")
    .replace("NA", None)
    .withColumn("name",F.coalesce("name","raw"))
    .dropDuplicates(["name"])
    .na.fill("NA")
    .withColumn("id", F.monotonically_increasing_id()+1)
    .select("id", F.col("name").alias("venue_name"))
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("dim_venue")
)

# dim fos general
(df
    .selectExpr("fos_general")
    .dropDuplicates(["fos_general"])
    .withColumn("id", F.monotonically_increasing_id()+1)
    .selectExpr("id", "fos_general")
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("dim_fos_general")
)

# dim fos specific
(df
    .selectExpr("fos_specific")
    .dropDuplicates(["fos_specific"])
    .withColumn("id", F.monotonically_increasing_id()+1)
    .selectExpr("id", "fos_specific")
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("dim_fos_specific")
)

# dim organization
(df
    .selectExpr("authors")
    .withColumn('authors', F.explode('authors'))
    .selectExpr("authors.org" )
    .dropDuplicates(["org"])
    .withColumn("id", F.monotonically_increasing_id()+1)
    .selectExpr("id", "org")
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("dim_organization")
)    

# dim author
df_temp = (df
    .selectExpr("authors")
    .withColumn('authors', F.explode('authors'))
    .selectExpr("authors.name" )
    .dropDuplicates(["name"])        
    .withColumn("FirstName",F.split(F.col("name")," ").getItem(0))
    .withColumn("MiddleName",F.split(F.col("name")," ").getItem(1))
    .withColumn("MiddleName_backup",F.split(F.col("name")," ").getItem(1))
    .withColumn("LastName",F.split(F.col("name")," ").getItem(2))
    .withColumn("LastName_backup",F.split(F.col("name")," ").getItem(2))
    .withColumn("LastName",F.coalesce("LastName","MiddleName"))
    .drop("name")
    .na.fill("NA")
    )

(df_temp.withColumn("MiddleName", F.when(df_temp.LastName_backup == "NA", "NA")
           .otherwise(df_temp.MiddleName))
#            .replace("NA", None)
           .withColumn("id", F.monotonically_increasing_id()+1)
           .selectExpr("id", "FirstName", "MiddleName", "LastName" )
           .write
           .format("delta")
           .mode("overwrite")
           .saveAsTable("dim_author")
)

del df_temp

# dim language
(df
    .selectExpr("lang")
    .dropDuplicates(["lang"])
    .withColumn("id", F.monotonically_increasing_id()+1)
    .selectExpr("id", "lang")
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("dim_language")
)


In [0]:
# data frames from delta tables

df_date = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/dim_date`")
df_doc_type = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/dim_doc_type`")
df_publication = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/dim_publication`")
df_venue = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/dim_venue`")
df_fos_general = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/dim_fos_general`")
df_fos_specific = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/dim_fos_specific`")
df_organization = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/dim_organization`")
df_author = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/dim_author`")
df_language = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/dim_language`")

df_date.createOrReplaceTempView("dim_date")
df_doc_type.createOrReplaceTempView("dim_doc_type")
df_publication.createOrReplaceTempView("dim_publication")
df_venue.createOrReplaceTempView("dim_venue")
df_fos_general.createOrReplaceTempView("dim_fos_general")
df_fos_specific.createOrReplaceTempView("dim_fos_specific")
df_organization.createOrReplaceTempView("dim_organization")
df_author.createOrReplaceTempView("dim_author")
df_language.createOrReplaceTempView("dim_language")


#### Fact table

In [0]:
# fact table
df = (df
    .drop("id", "abstract", "keywords", "issn", "isbn", "volume", "doi", "n_citation")

    # authors flattening
    .select("*", F.posexplode("authors"))
    .select("*", F.col("pos").alias("author_rank"), "col.*")

    .withColumn("FirstName",F.split(F.col("name")," ").getItem(0))
    .withColumn("MiddleName",F.split(F.col("name")," ").getItem(1))
    .withColumn("MiddleName_backup",F.split(F.col("name")," ").getItem(1))
    .withColumn("LastName",F.split(F.col("name")," ").getItem(2))
    .withColumn("LastName_backup",F.split(F.col("name")," ").getItem(2))
    .withColumn("LastName",F.coalesce("LastName","MiddleName"))
    .drop("name", "pos", "col", "authors")
    .na.fill("NA")
    # .select("*", authors_udf("MiddleName", "LastName_backup"))
)

df = (df
    .withColumn("MiddleName", F.when(df.LastName_backup == "NA", "NA")
    .otherwise(df.MiddleName))
    .drop("MiddleName_backup", "LastName_backup")
        
    # venue flattening
    .select("*", "venue.*")
    .replace("NA", None)
    .withColumn("venue_name", F.coalesce("name","raw"))
    .drop("name", "raw", "venue", "type")
    .na.fill("NA")
    
    # date/year
    .join(df_date, "year")
    .select(F.col("id").alias("date_id"), "*")
    .drop("year", "id")

    # doc_type
    .join(df_doc_type, "doc_type")
    .select(F.col("id").alias("doc_type_id"), "*")
    .drop("doc_type", "id")

    # publication / title
    .join(df_publication, "title")
    .select(F.col("id").alias("publication_id"), "*")
    .drop("volume", "issn", "isbn", "doi", "n_citation", "title", "id")

    # venue
    .join(df_venue, "venue_name")
    .select(F.col("id").alias("venue_id"), "*")
    .drop("venue_name", "id")

    # fos general
    .join(df_fos_general, "fos_general")
    .select(F.col("id").alias("fos_general_id"), "*")
    .drop("fos_general", "id")

    # fos specific
    .join(df_fos_specific, "fos_specific")
    .select(F.col("id").alias("fos_specific_id"), "*")
    .drop("fos_specific", "id")
        
    # organization
    .join(df_organization, "org")
    .select(F.col("id").alias("org_id"), "*")
    .drop("org", "id")
    
    # language
    .join(df_language, "lang")
    .select(F.col("id").alias("language_id"), "*")
    .drop("lang", "id")
)

# author
df = (df
    .join(df_author, (df.FirstName == df_author.FirstName)
                     & (df.MiddleName == df_author.MiddleName)
                     & (df.LastName == df_author.LastName)
         )
    .select(F.col("id").alias("author_id"), "*")
    .drop("id", "FirstName", "MiddleName", "LastName")
    .withColumn("author_rank", df.author_rank+1)
    .select("date_id", "doc_type_id", "publication_id", "venue_id", "fos_general_id", "fos_specific_id", "org_id", "author_id", "language_id", "author_rank")
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("fact_dblp")
)

del df
                           

In [0]:
%fs

ls /user/hive/warehouse/fact_dblp/

path name size modificationTime dbfs:/user/hive/warehouse/fact_dblp/_delta_log/ _delta_log/ 0 0 dbfs:/user/hive/warehouse/fact_dblp/part-00000-3c5a6ab6-3cbc-4da5-af7d-7dbcd9e29018-c000.snappy.parquet part-00000-3c5a6ab6-3cbc-4da5-af7d-7dbcd9e29018-c000.snappy.parquet 15269503 1654626543000 dbfs:/user/hive/warehouse/fact_dblp/part-00001-8bb69190-6000-4b0f-b991-6beaf0f79a2a-c000.snappy.parquet part-00001-8bb69190-6000-4b0f-b991-6beaf0f79a2a-c000.snappy.parquet 15424336 1654626545000 dbfs:/user/hive/warehouse/fact_dblp/part-00002-170515b7-3f33-44e1-a750-75cc4c0743e6-c000.snappy.parquet part-00002-170515b7-3f33-44e1-a750-75cc4c0743e6-c000.snappy.parquet 15375910 1654626543000 dbfs:/user/hive/warehouse/fact_dblp/part-00003-89ffdf85-7fdf-4d4e-95ea-4c4953f122cb-c000.snappy.parquet part-00003-89ffdf85-7fdf-4d4e-95ea-4c4953f122cb-c000.snappy.parquet 15423639 1654626545000 dbfs:/user/hive/warehouse/fact_dblp/part-00004-59f6cc1d-2187-4ed3-8c8d-b1f5cb947605-c000.snappy.parquet part-00004-59f6cc1d-2187-4ed3-8c8d-b1f5cb947605-c000.snappy.parquet 15414746 1654626545000 dbfs:/user/hive/warehouse/fact_dblp/part-00005-b9801452-ae42-45fa-8f18-1a38dedd1844-c000.snappy.parquet part-00005-b9801452-ae42-45fa-8f18-1a38dedd1844-c000.snappy.parquet 14715322 1654626540000 dbfs:/user/hive/warehouse/fact_dblp/part-00006-6c52ae5f-f993-433b-a0d1-47aef5345725-c000.snappy.parquet part-00006-6c52ae5f-f993-433b-a0d1-47aef5345725-c000.snappy.parquet 15184920 1654626541000 dbfs:/user/hive/warehouse/fact_dblp/part-00007-b8d4c3be-a483-4825-a29c-729a9a1e4caf-c000.snappy.parquet part-00007-b8d4c3be-a483-4825-a29c-729a9a1e4caf-c000.snappy.parquet 15346548 1654626545000 dbfs:/user/hive/warehouse/fact_dblp/part-00008-de87c0a6-f223-40b8-a45c-8414cd9272b8-c000.snappy.parquet part-00008-de87c0a6-f223-40b8-a45c-8414cd9272b8-c000.snappy.parquet 15657366 1654626559000 dbfs:/user/hive/warehouse/fact_dblp/part-00009-3fdd8f03-003e-4fbc-bfeb-1c5680b34fe3-c000.snappy.parquet part-00009-3fdd8f03-003e-4fbc-bfeb-1c5680b34fe3-c000.snappy.parquet 15743956 1654626560000 dbfs:/user/hive/warehouse/fact_dblp/part-00010-ab68a88b-dbf1-4b77-8ae7-024bf384cd10-c000.snappy.parquet part-00010-ab68a88b-dbf1-4b77-8ae7-024bf384cd10-c000.snappy.parquet 9975483 1654626557000

In [0]:
# data frames from delta tables

df_bdlp = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/fact_dblp`")
df_bdlp.createOrReplaceTempView("fact_dblp")


In [0]:
display(df_bdlp)
display(df_bdlp.count())
display(df_bdlp.printSchema())


date_id doc_type_id publication_id venue_id fos_general_id fos_specific_id org_id author_id language_id author_rank 100 1 8589990338 17179870565 6 6 60129547352 25770092289 1 1 105 1 17180277236 25769805978 1 6 8589940963 25769958724 1 3 107 1 17180048281 1722 1 6 25769901315 17180023505 1 2 106 2 60129688127 42949674281 6 8 17179985220 25769964495 1 3 87 1 60129636876 8589934972 6 19 8589940963 172341 1 1 99 1 42949958938 60129543404 6 8 8589940963 51539697127 1 2 103 2 209592 42949674458 6 8 17179979304 51539697127 1 2 93 8 60129668208 51539608208 1 6 8589940963 14839 1 4 113 1 8590191779 60129547085 1 6 34359754834 51539900834 1 2 82 1 17180205086 34359739442 1 6 8589940963 34359824296 1 2 90 2 42949906510 8589935183 6 20 8589940963 112561 1 1 108 2 8590238674 42949673157 6 38 100187 25770035170 1 5 108 2 8590238674 42949673157 6 38 100187 68719507585 1 5 98 2 34359961968 51539608575 1 6 42949843144 25770035170 1 1 98 2 34359961968 51539608575 1 6 42949843144 68719507585 1 1 108 1 34359836563 17179869476 6 3 25769825179 48741 1 1 94 2 25770039545 8589935183 6 20 8589940963 170913 1 16 109 2 25770113536 51539608575 3 17 34359860049 25769979842 1 7 87 1 266367 60129542686 6 38 8589940963 8590003978 1 3 110 2 25770210484 51539607790 6 8 8589940963 51539816912 1 4 97 1 25770197172 25769804937 1 6 8589940963 8589988953 1 1 96 1 51539774185 17179871092 1 6 51539664207 8590034867 1 4 101 2 60129803867 51539608575 6 8 17179962560 68719485589 1 3 106 2 34359977921 51539608575 3 17 42949702599 68719485589 1 11 104 2 42949770431 51539608575 3 17 42949702599 68719485589 1 4 82 1 25769937767 1627 6 6 60129568787 42949729267 1 2 109 4 42950023766 42949674418 4 1 8589940963 60129768904 1 2 94 1 143470 51539608502 6 20 42949768951 51539753753 1 2 103 1 17180242771 34359739221 3 17 8589940963 60129641364 1 5 108 2 8590142713 51539608575 6 8 60129556991 60129641364 1 4 107 1 167431 17179869810 6 38 60129548128 25769860793 1 15 93 1 25770056145 42949674671 6 6 60129711853 60129773156 1 2 102 2 60129629933 51539608575 3 17 25769945479 42949866985 1 4 84 2 34359855436 8589935183 6 20 8589940963 42949817548 1 3 96 2 60129779077 412 6 19 51539609576 60129558212 1 2 106 1 60129942305 17179870881 3 17 25769937697 8590110685 1 3 102 2 245487 17179870071 6 38 42949723151 8590123690 1 2 95 4 17180247311 60129543888 6 20 8589940963 51539722590 1 4 95 2 25770178761 25769804894 6 20 8589940963 51539722590 1 3 97 4 25770167438 60129543888 6 20 8589940963 51539722590 1 3 97 4 34359929031 60129542402 6 38 8589940963 51539722590 1 3 95 4 42949867257 60129543888 6 20 8589940963 51539722590 1 3 96 4 17180254557 60129543888 6 20 34359837980 51539722590 1 3 92 2 367323 60129542711 1 6 8589940963 118143 1 3 93 4 68719486043 1724 1 6 8589940963 118143 1 3 94 4 34359985786 1724 2 10 8589940963 118143 1 2 102 1 51539688087 34359739221 2 10 8589940963 34359789100 1 5 102 2 107587 51539608575 3 17 8590025967 34359789100 1 6 97 4 25769806918 60129542402 6 6 8589940963 17180061378 1 2 83 1 74719 51539608426 6 8 42949699694 34359885917 1 2 95 1 162667 2699 6 38 8589940963 60129784941 1 2 109 2 17180250655 8589935183 6 20 8589940963 17180051775 1 7 99 1 60129876276 42949674176 6 6 8589940963 8590049657 1 2 97 1 34359993493 42949674242 6 8 8589940963 8590049657 1 2 98 1 8590280291 34359739466 1 6 25769903478 8590049657 1 1 110 1 42949836883 42949674418 1 6 8589940963 60129764185 1 4 97 1 42949971711 51539608060 6 38 8589940963 17180084274 1 4 94 1 17180253986 51539608060 3 30 8589940963 17180084274 1 4 94 1 68719493091 25769804937 1 6 8589940963 34359901100 1 2 82 1 51539975983 51539607708 1 6 8589940963 60129711128 1 1 107 1 34359913250 42949674418 6 16 8589940963 60129781525 1 2 76 2 8590016113 3089 1 6 8589940963 8590044092 1 3 102 2 84223 51539608575 2 10 60129586011 8590006551 1 8 81 8 51539881176 42949674090 1 6 10766 34359853019 1 2 109 4 17180051997 34359741230 6 38 42949720202 17179966266 1 11 105 1 34359839510 34359739453 1 6 51539624884 60129714940 1 3 94 1 4295

10852684root
 |-- date_id: long (nullable = true)
 |-- doc_type_id: long (nullable = true)
 |-- publication_id: long (nullable = true)
 |-- venue_id: long (nullable = true)
 |-- fos_general_id: long (nullable = true)
 |-- fos_specific_id: long (nullable = true)
 |-- org_id: long (nullable = true)
 |-- author_id: long (nullable = true)
 |-- language_id: long (nullable = true)
 |-- author_rank: integer (nullable = true)



### DWH Queries

- top k authors based on their h-index that publish in the field "computer sciences"

In [0]:
### Query top-k authors, based on their H-index that publish in a specific fos

# The h-index is calculated by counting the number of publications for which an author has been cited by other authors at least that same number of times.
# For instance, an h-index of 17 means that the scientist has published at least 17 papers that have each been cited at least 17 times. 


In [0]:
# spark 'query' to the fcat table
(df_bdlp
    .select("publication_id", "fos_general_id", "fos_specific_id", "author_id", "author_rank")
    .join(df_publication, (df_bdlp.publication_id == df_publication.id))
    .drop("publication_id", "volume", "issn", "isbn", "doi", "id")
    .join(df_author, (df_bdlp.author_id == df_author.id))
    .drop("id", "author_id")
    .join(df_fos_general, (df_bdlp.fos_general_id == df_fos_general.id))
    .drop("fos_general_id", "id")
    .join(df_fos_specific, (df_bdlp.fos_specific_id == df_fos_specific.id))
    .drop("fos_specific_id", "id")
    .filter(F.col("fos_specific") == "computer sciences")
    .drop("fos_general", "author_rank")
    .replace("NA", None)
    .withColumn("FullName", F.concat_ws(',', F.col("FirstName"),F.col("MiddleName"),F.col("LastName")))
    .drop("FirstName", "MiddleName", "LastName")
    .select(F.col("FullName").alias("Author"), F.col("n_citation").alias("PaperCitation"))
    .filter(F.col("Author") != "")
    .write
    .saveAsTable("df_hindex")
)



In [0]:
df_hindex = spark.sql("SELECT * FROM delta.`/user/hive/warehouse/df_hindex`")
df_hindex.createOrReplaceTempView("df_hindex")

display(df_hindex)
display(df_hindex.count())

Author PaperCitation Hod,Lipson 42 Hod,Lipson 186 Hod,Lipson 4 Hod,Lipson 83 Hod,Lipson 40 Hod,Lipson 305 Hod,Lipson 5497 Hod,Lipson 95 Hod,Lipson 8 Hod,Lipson 19 Hod,Lipson 3 Hod,Lipson 30 Hod,Lipson 2 Hod,Lipson 160 Hod,Lipson 16 Hod,Lipson 6 Hod,Lipson 1 Hod,Lipson 2 Hod,Lipson 62 Hod,Lipson 10 Hod,Lipson 41 Hod,Lipson 39 Hod,Lipson 13 Hod,Lipson 25 Hod,Lipson 49 Hod,Lipson 35 Hod,Lipson 8 Hod,Lipson 145 Hod,Lipson 4 Hod,Lipson 30 Hod,Lipson 88 Hod,Lipson 17 Hod,Lipson 16 Hod,Lipson 5 Hod,Lipson 25 Hod,Lipson 7 Hod,Lipson 104 Hod,Lipson 8 Hod,Lipson 3 Hod,Lipson 22 Hod,Lipson 91 Hod,Lipson 1 Hod,Lipson 101 Hod,Lipson 26 Hod,Lipson 10 Hod,Lipson 2 Hod,Lipson 32 Hod,Lipson 11 Hod,Lipson 101 Hod,Lipson 4 Hod,Lipson 30 Hod,Lipson 29 Hod,Lipson 12 Hod,Lipson 3 Hod,Lipson 24 Hod,Lipson 33 Daniel,J.,Kleitman 5 Pearl,Pu 99 Pearl,Pu 33 Pearl,Pu 30 Pearl,Pu 8 Pearl,Pu 1 Pearl,Pu 1 Pearl,Pu 11 Pearl,Pu 36 Pearl,Pu 39 Pearl,Pu 5 Pearl,Pu 106 Pearl,Pu 1 Pearl,Pu 6 Pearl,Pu 5 Pearl,Pu 3 Pearl,Pu 61 Pearl,Pu 29 Pearl,Pu 7 Pearl,Pu 53 Jeffrey,T.,Hancock 14 Jeffrey,T.,Hancock 15 Lukasz,Golab 1 Lukasz,Golab 57 Lukasz,Golab 5 Lukasz,Golab 6 Lukasz,Golab 24 Lukasz,Golab 12 Lukasz,Golab 26 Lukasz,Golab 20 Lukasz,Golab 31 Lukasz,Golab 3 Lukasz,Golab 8 Lukasz,Golab 2 Lukasz,Golab 384 Lukasz,Golab 20 Yannis,Tzitzikas 10 Yannis,Tzitzikas 1 Yannis,Tzitzikas 17 Yannis,Tzitzikas 3 Yannis,Tzitzikas 2 Yannis,Tzitzikas 4 Yannis,Tzitzikas 20 Yannis,Tzitzikas 8 Yannis,Tzitzikas 7 Alan,Dix 4 Alan,Dix 13 Alan,Dix 10 Alan,Dix 129 Alan,Dix 45 Alan,Dix 23 Alan,Dix 25 Alan,Dix 2 Alan,Dix 44 Alan,Dix 21 Philippe,Dessus 20 Philippe,Dessus 10 Philippe,Dessus 9 Philippe,Dessus 40 Philippe,Dessus 63 Philippe,Dessus 12 Philippe,Dessus 1 Philippe,Dessus 4 Philippe,Dessus 23 Philippe,Dessus 1 Philippe,Dessus 3 Seyed,Mohammad,Ghoreyshi 8 Seyed,Mohammad,Ghoreyshi 12 Margner,,V 42 Margner,,V 39 Margner,,V 4 Margner,,V 2 Chong,Jiang 1 Norman,Chonacky 2 Luciano,da,F. 3 Luciano,da,F. 43 Luciano,da,F. 5 Luciano,da,F. 87 Luciano,da,F. 7 Luciano,da,F. 3 Luciano,da,F. 61 Luciano,da,F. 6 Luciano,da,F. 1 Luciano,da,F. 6 Luciano,da,F. 3 Luciano,da,F. 12 Jason,Hiser 27 Jason,Hiser 6 Jason,Hiser 3 Jason,Hiser 10 Jason,Hiser 325 Jason,Hiser 132 Jason,Hiser 25 Jason,Hiser 31 Jason,Hiser 1 Senén,Barro 36 Senén,Barro 1 Senén,Barro 7 Senén,Barro 1381 Senén,Barro 4 Senén,Barro 3 Senén,Barro 6 Senén,Barro 51 Senén,Barro 11 Senén,Barro 4 Senén,Barro 7 Senén,Barro 6 Senén,Barro 32 Senén,Barro 16 Senén,Barro 3 Senén,Barro 4 Senén,Barro 10 Senén,Barro 27 Senén,Barro 1 Senén,Barro 3 Senén,Barro 7 Senén,Barro 74 Senén,Barro 87 Senén,Barro 8 Senén,Barro 1 Senén,Barro 14 Senén,Barro 16 Senén,Barro 18 Senén,Barro 5 Senén,Barro 1 Senén,Barro 2 Senén,Barro 6 Senén,Barro 8 Senén,Barro 5 Senén,Barro 6 Jesus,Ubaldo,Quevedo-Torrero 1 Jorge,Gonzalez 16 Erwin,Mayer 38 Erwin,Mayer 6 Fiana,Raiber 30 Fiana,Raiber 5 Brent,Bryan 54 Julien,Pettré 67 Julien,Pettré 14 Julien,Pettré 10 Julien,Pettré 7 Julien,Pettré 23 Julien,Pettré 5 Julien,Pettré 75 Julien,Pettré 4 Julien,Pettré 87 Julien,Pettré 45 Julien,Pettré 149 Julien,Pettré 7 Julien,Pettré 272 Julien,Pettré 2 Julien,Pettré 28 Julien,Pettré 11 Julien,Pettré 19 Julien,Pettré 3 Julien,Pettré 6 Julien,Pettré 119 Julien,Pettré 10 Julien,Pettré 8 Julien,Pettré 1 Julien,Pettré 37 Julien,Pettré 8 Julien,Pettré 31 Julien,Pettré 4 Julien,Pettré 41 Julien,Pettré 85 Julien,Pettré 15 Julien,Pettré 5 Julien,Pettré 49 Julien,Pettré 13 Julien,Pettré 122 Julien,Pettré 11 Julien,Pettré 31 Julien,Pettré 1 Julien,Pettré 6 Julien,Pettré 11 Julien,Pettré 12 Julien,Pettré 9 Nick,Tredennick 6 Nick,Tredennick 14 Nick,Tredennick 1 Francis,Wray 5 Francis,Wray 3 Francis,Wray 1 Walter,S.,Lasecki 30 Walter,S.,Lasecki 110 Walter,S.,Lasecki 20 Walter,S.,Lasecki 22 Walter,S.,Lasecki 16 Walter,S.,Lasecki 7 Walter,S.,Lasecki 2 Walter,S.,Lasecki 37 Walter,S.,Lasecki 7 Walter,S.,Lasecki 14 Walter,S.,Lasecki 8 Walter,S.,Lasecki 13 Walter,S.,Lasecki 2 S.,Sahni 2 S.,Sahni 19 S.,Sahni 28 S.,Sahni 143

2978124

In [0]:
hindex_df = (spark.sql("""
SELECT Author, MAX(Ranking) AS Hindex
FROM (SELECT Author, PaperCitation, ROW_NUMBER() OVER (PARTITION BY Author ORDER BY PaperCitation DESC) AS Ranking
    FROM df_hindex)
WHERE Ranking <= PaperCitation
GROUP BY Author
ORDER BY MAX(Ranking) DESC
"""))

In [0]:
display(hindex_df)

Author Hindex Anil,K.,Jain 154 Wil,M.,P. 134 Andrew,Zisserman 126 Yoshua,Bengio 124 A.,H.,M. 124 Jitendra,Malik 112 Xiaoou,Tang 112 Thomas,S.,Huang 111 Dacheng,Tao 111 Xiaogang,Wang 111 Lei,Zhang 110 Sebastian,Thrun 108 J.,M.,M. 105 Ming-Hsuan,Yang 104 Cordelia,Schmid 104 A.,J.,M. 102 Bernt,Schiele 101 Trevor,Darrell 101 Arthur,H.,M. 100 Shuicheng,Yan 99 María,del,Carmen 99 Xuelong,Li 97 Christopher,D.,Manning 96 Takeo,Kanade 93 Mubarak,Shah 92 Rajkumar,Buyya 90 Wolfram,Burgard 89 Luc,Van,Gool 89 Andrew,Y.,Ng 88 David,Zhang 87 Stan,Z.,Li 87 Pascal,Fua 87 Ion,Stoica 86 Fernando,De,la 86 Larry,S.,Davis 85 Shree,K.,Nayar 85 Marc,Pollefeys 84 Dieter,Fox 84 Yi,Yang 84 Rama,Chellappa 84 Richard,Szeliski 83 Martial,Hebert 83 Michael,J.,Black 82 Ian,D.,Reid 82 Jian,Sun 81 Tieniu,Tan 81 Geoffrey,E.,Hinton 81 Philip,S.,Yu 80 Shaogang,Gong 80 Hermann,Ney 80 Pieter,Abbeel 79 Scott,Shenker 79 B.,V.,K. 78 William,T.,Freeman 77 Sergey,Levine 77 Wen,Gao 76 Robert,E.,Schapire 76 Zhi-Hua,Zhou 76 Luc,J.,Van 75 Antonio,Torralba 75 Daniel,Cremers 75 Hans-Peter,Seidel 75 Raquel,Urtasun 75 A.,K.,M. 73 Qiang,Yang 73 Qi,Tian 73 Roland,Siegwart 73 Roberto,Cipolla 72 Jiaya,Jia 72 Kristen,Grauman 71 Daphne,Koller 70 Michael,I.,Jordan 69 Bernhard,Schölkopf 69 Jack,Dongarra 69 A.,Murat,Tekalp 68 Peter,Stone 68 Shih-Fu,Chang 68 Li,Fei-Fei 68 Alan,L.,Yuille 68 Dan,Roth 68 Laurens,van,der 68 Chunhua,Shen 68 Jürgen,Schmidhuber 67 Wei,Zhang 67 Pietro,Perona 67 Frédo,Durand 67 Alexei,A.,Efros 67 Thomas,Brox 66 Daniel,Rueckert 65 Philip,H.,S. 65 W.,M.,P. 65 Jiebo,Luo 65 Yang,Liu 65 Wei,Li 64 Christian,Theobalt 64 Narendra,Ahuja 64 Li,Zhang 64 Ruslan,Salakhutdinov 63 Shiguang,Shan 63 Gang,Wang 63 Daniel,Cohen-Or 63 Mirella,Lapata 63 Dinesh,Manocha 63 Liang,Wang 63 Wanli,Ouyang 63 Huchuan,Lu 62 Dinggang,Shen 62 Jiawei,Han 62 Raymond,J.,Mooney 62 Silvio,Savarese 62 Steven,C.,H. 62 Wei,Liu 61 Matti,Pietikäinen 61 Hui,Zhang 61 Leonidas,J.,Guibas 61 Francisco,Herrera 61 Tao,Xiang 61 Wei,Wang 61 Zhengyou,Zhang 61 Deva,Ramanan 61 Horst,Bischof 61 Xilin,Chen 61 Yann,LeCun 61 Heung-Yeung,Shum 61 Li,Deng 61 Eric,P.,Xing 61 Liang,Lin 60 Abhinav,Gupta 60 Zoubin,Ghahramani 60 Pushmeet,Kohli 60 Guillermo,Sapiro 60 B.,S.,Manjunath 60 Andrea,Vedaldi 60 Jie,Wu 59 Jie,Yang 59 Chen,Change,Loy 59 Vincent,Lepetit 59 Michael,F.,P. 59 Jun,Wang 59 Dong,Xu 58 Qiang,Ji 58 Michael,J.,Carey 58 Nicu,Sebe 58 Gaurav,S.,Sukhatme 58 Richard,G.,Baraniuk 58 Bo,Li 58 Yu,Wang 58 Davide,Scaramuzza 58 Honglak,Lee 58 Ying,Wu 58 Noah,A.,Smith 58 Stefano,Soatto 58 Zhen,Lei 58 Andrew,W.,Moore 57 Jian,Yang 57 Yi,Ma 57 Samy,Bengio 57 Weisi,Lin 57 William,J.,Dally 57 Chris,Dyer 57 Dan,Klein 57 Ling,Shao 57 Yun,Fu 56 Jiashi,Feng 56 Baochun,Li 56 Carsten,Rother 56 Victor,C.,M. 56 Jennifer,Rexford 56 Xinbo,Gao 56 Nassir,Navab 56 Ben,J.,A. 56 Liangpei,Zhang 56 James,M.,Rehg 56 Daniela,Rus 56 Josef,Kittler 56 Mark,D.,Hill 55 Vijay,Kumar 55 Nicholas,Ayache 55 Ramesh,Raskar 55 Wangmeng,Zuo 55 Stephen,Lin 55 Chin-Hui,Lee 55 Maja,Pantic 55 Vincent,W.,S. 55 Edward,J.,Delp 55 Xiang,Bai 55 Andrew,McCallum 55 Ming,Zhou 55 Nicholas,R.,Jennings 55 Sing,Bing,Kang 55 S.,M.,Ali 54 Dong,Yu 54 André,van,der 54 Haibin,Ling 54 Xiaokang,Yang 54 Katsushi,Ikeuchi 54 Andrew,J.,Davison 54 Nuno,Vasconcelos 54 Meng,Wang 54 John,A.,Stankovic 54 Song-Chun,Zhu 54 Horst,Bunke 54 Quoc,V.,Le 54 Jiwen,Lu 54 H.,Van,Dyke 54 Tao,Mei 54 Onur,Mutlu 54 Jingdong,Wang 53 Aaron,F.,Bobick 53 Stan,Sclaroff 53 Jianfeng,Gao 53 Junsong,Yuan 53 Robert,A.,van 53 Yuan,Yuan 53 Stefan,Schaal 53 Kostas,Daniilidis 53 Pat,Hanrahan 53 Zeshui,Xu 53 M.,van,der 53 Andrew,Blake 53 K.,J.,Ray 53 Jean,Ponce 52 Rachid,Guerraoui 52 Vladlen,Koltun 52 Marco,Dorigo 52 Yale,N.,Patt 52 Feiping,Nie 52 Chenyang,Lu 52 Kevin,W.,Bowyer 52 U.,Rajendra,Acharya 52 Lawrence,Carin 52 P.,Sadayappan 52 Hao,Zhang 52 Konrad,Schindler 52 Oriol,Vinyals 52 Ravi,Ramamoorthi 52 Yang,Wang 52 Zhuowen,Tu 52 Jason,Weston 52 Luca,Maria,Gambardella 52 Andreas,Stolcke 52 Henri,Prade 52 Manuela,M.,Veloso 51

In [0]:
# pandas-based solution for the h-index query
# https://stackoverflow.com/questions/29671726/efficient-way-to-calculate-h-index-impact-productivity-of-author-publication-i

# pd_df_hindex = df_hindex.toPandas()
# pd_df_hindex = pd_df_hindex.sort_values(by=["Author","PaperCitation"], ascending=[1,0])
# groups = pd_df_hindex.groupby("Author")

# ind2 = np.array([np.arange(len(g))+1 for g in groups.groups.values()],dtype=object)
# pd_df_hindex['newindex'] = np.hstack(ind2)
# pd_df_hindex['condition'] = pd_df_hindex['PaperCitation'] >= pd_df_hindex['newindex']
# hindex = pd_df_hindex.groupby('Author').sum()['condition']

# df_hindex = (pd.DataFrame({"Author":list(hindex.index), "h-index":hindex.values}))
# df_hindex = df_hindex.sort_values(by=["h-index"], ascending=[0])
# display(df_hindex)


In [0]:
display(df_hindex)

Author h-index Anil,K.,Jain 154 Wil,M.,P. 134 Andrew,Zisserman 126 A.,H.,M. 124 Yoshua,Bengio 124 Jitendra,Malik 112 Xiaoou,Tang 112 Thomas,S.,Huang 111 Xiaogang,Wang 111 Dacheng,Tao 111 Lei,Zhang 110 Sebastian,Thrun 108 J.,M.,M. 105 Cordelia,Schmid 104 Ming-Hsuan,Yang 104 A.,J.,M. 102 Bernt,Schiele 101 Trevor,Darrell 101 Arthur,H.,M. 100 Shuicheng,Yan 99 María,del,Carmen 99 Xuelong,Li 97 Christopher,D.,Manning 96 Takeo,Kanade 93 Mubarak,Shah 92 Rajkumar,Buyya 90 Wolfram,Burgard 89 Luc,Van,Gool 89 Andrew,Y.,Ng 88 David,Zhang 87 Stan,Z.,Li 87 Pascal,Fua 87 Ion,Stoica 86 Fernando,De,la 86 Larry,S.,Davis 85 Shree,K.,Nayar 85 Yi,Yang 84 Marc,Pollefeys 84 Dieter,Fox 84 Rama,Chellappa 84 Richard,Szeliski 83 Martial,Hebert 83 Ian,D.,Reid 82 Michael,J.,Black 82 Jian,Sun 81 Tieniu,Tan 81 Geoffrey,E.,Hinton 81 Philip,S.,Yu 80 Shaogang,Gong 80 Hermann,Ney 80 Scott,Shenker 79 Pieter,Abbeel 79 B.,V.,K. 78 Sergey,Levine 77 William,T.,Freeman 77 Robert,E.,Schapire 76 Wen,Gao 76 Zhi-Hua,Zhou 76 Daniel,Cremers 75 Hans-Peter,Seidel 75 Raquel,Urtasun 75 Antonio,Torralba 75 Luc,J.,Van 75 Roland,Siegwart 73 Qi,Tian 73 Qiang,Yang 73 A.,K.,M. 73 Jiaya,Jia 72 Roberto,Cipolla 72 Kristen,Grauman 71 Daphne,Koller 70 Jack,Dongarra 69 Michael,I.,Jordan 69 Bernhard,Schölkopf 69 A.,Murat,Tekalp 68 Dan,Roth 68 Peter,Stone 68 Shih-Fu,Chang 68 Li,Fei-Fei 68 Alan,L.,Yuille 68 Laurens,van,der 68 Chunhua,Shen 68 Wei,Zhang 67 Jürgen,Schmidhuber 67 Frédo,Durand 67 Alexei,A.,Efros 67 Pietro,Perona 67 Thomas,Brox 66 Jiebo,Luo 65 Yang,Liu 65 W.,M.,P. 65 Daniel,Rueckert 65 Philip,H.,S. 65 Li,Zhang 64 Christian,Theobalt 64 Narendra,Ahuja 64 Wei,Li 64 Wanli,Ouyang 63 Daniel,Cohen-Or 63 Gang,Wang 63 Dinesh,Manocha 63 Shiguang,Shan 63 Liang,Wang 63 Mirella,Lapata 63 Ruslan,Salakhutdinov 63 Jiawei,Han 62 Huchuan,Lu 62 Raymond,J.,Mooney 62 Dinggang,Shen 62 Silvio,Savarese 62 Steven,C.,H. 62 Zhengyou,Zhang 61 Tao,Xiang 61 Xilin,Chen 61 Horst,Bischof 61 Leonidas,J.,Guibas 61 Deva,Ramanan 61 Heung-Yeung,Shum 61 Wei,Liu 61 Li,Deng 61 Yann,LeCun 61 Eric,P.,Xing 61 Matti,Pietikäinen 61 Hui,Zhang 61 Wei,Wang 61 Francisco,Herrera 61 Pushmeet,Kohli 60 B.,S.,Manjunath 60 Liang,Lin 60 Abhinav,Gupta 60 Zoubin,Ghahramani 60 Andrea,Vedaldi 60 Guillermo,Sapiro 60 Vincent,Lepetit 59 Jie,Wu 59 Chen,Change,Loy 59 Michael,F.,P. 59 Jie,Yang 59 Jun,Wang 59 Michael,J.,Carey 58 Gaurav,S.,Sukhatme 58 Richard,G.,Baraniuk 58 Ying,Wu 58 Zhen,Lei 58 Dong,Xu 58 Stefano,Soatto 58 Nicu,Sebe 58 Yu,Wang 58 Noah,A.,Smith 58 Davide,Scaramuzza 58 Qiang,Ji 58 Bo,Li 58 Honglak,Lee 58 Ling,Shao 57 Jian,Yang 57 William,J.,Dally 57 Dan,Klein 57 Weisi,Lin 57 Yi,Ma 57 Andrew,W.,Moore 57 Chris,Dyer 57 Samy,Bengio 57 Carsten,Rother 56 Nassir,Navab 56 Jiashi,Feng 56 Liangpei,Zhang 56 Ben,J.,A. 56 Yun,Fu 56 Xinbo,Gao 56 Josef,Kittler 56 James,M.,Rehg 56 Victor,C.,M. 56 Daniela,Rus 56 Jennifer,Rexford 56 Baochun,Li 56 Xiang,Bai 55 Ming,Zhou 55 Nicholas,Ayache 55 Wangmeng,Zuo 55 Ramesh,Raskar 55 Vincent,W.,S. 55 Mark,D.,Hill 55 Edward,J.,Delp 55 Vijay,Kumar 55 Andrew,McCallum 55 Stephen,Lin 55 Chin-Hui,Lee 55 Sing,Bing,Kang 55 Nicholas,R.,Jennings 55 Maja,Pantic 55 Quoc,V.,Le 54 Jiwen,Lu 54 H.,Van,Dyke 54 Katsushi,Ikeuchi 54 Andrew,J.,Davison 54 Haibin,Ling 54 Onur,Mutlu 54 Tao,Mei 54 Nuno,Vasconcelos 54 Song-Chun,Zhu 54 Meng,Wang 54 John,A.,Stankovic 54 André,van,der 54 S.,M.,Ali 54 Dong,Yu 54 Xiaokang,Yang 54 Horst,Bunke 54 Pat,Hanrahan 53 Aaron,F.,Bobick 53 Yuan,Yuan 53 Zeshui,Xu 53 Kostas,Daniilidis 53 Junsong,Yuan 53 Jianfeng,Gao 53 Stan,Sclaroff 53 Stefan,Schaal 53 K.,J.,Ray 53 Jingdong,Wang 53 Robert,A.,van 53 M.,van,der 53 Andrew,Blake 53 Ravi,Ramamoorthi 52 Rachid,Guerraoui 52 Yale,N.,Patt 52 Luca,Maria,Gambardella 52 Jason,Weston 52 U.,Rajendra,Acharya 52 Kevin,W.,Bowyer 52 Lawrence,Carin 52 Oriol,Vinyals 52 Vladlen,Koltun 52 Chenyang,Lu 52 P.,Sadayappan 52 Zhuowen,Tu 52 Jean,Ponce 52 Yang,Wang 52 Marco,Dorigo 52 Feiping,Nie 52 Konrad,Schindler 52 Henri,Prade 52 Hao,Zhang 52 Andreas,Stolcke 52 Tinne,Tuytelaars 51

### API Queries

#### Gender API

In [0]:
pd_hindex_df = hindex_df.limit(500).toPandas()

In [0]:
top_500_authors = (pd_hindex_df
        .Author
        .tolist()
)

for i in range(0, len(top_500_authors)):
    top_500_authors[i] = top_500_authors[i].replace(",", " ")


In [0]:
my_genders = []

for i in range(20, len(top_500_authors)):
    
    author = top_500_authors[i].split()
    if len(author) == 3:
        firsrname = unidecode(author[0]).replace('.', '')
        lastname = unidecode(author[2]).replace('.', '')
    else:
        firsrname = unidecode(author[0]).replace('.', '')
        lastname = unidecode(author[1]).replace('.', '')
        
    print(i, firsrname, lastname)
    
    myKey = "sUae6FCgrVhPNtwK3W6FTh3nMBbMmtLRwACw"
    # url = "https://gender-api.com/get?key=" + myKey + "&name={}".format('Anil K Jain')
    url = "https://gender-api.com/get?split={}%20{}&key={}".format(firsrname, lastname, myKey)
    response = urlopen(url)
    decoded = response.read().decode('utf-8')
    data = json.loads(decoded)
    
    my_genders.append(data["gender"])


20 Maria Carmen
21 Xuelong Li
22 Christopher Manning
23 Takeo Kanade
24 Mubarak Shah
25 Rajkumar Buyya
26 Luc Gool
27 Wolfram Burgard
28 Andrew Ng
29 Stan Li
30 Pascal Fua
31 David Zhang
32 Fernando la
33 Ion Stoica
34 Larry Davis
35 Shree Nayar
36 Marc Pollefeys
37 Rama Chellappa
38 Yi Yang
39 Dieter Fox
40 Martial Hebert
41 Richard Szeliski
42 Ian Reid
43 Michael Black
44 Jian Sun
45 Tieniu Tan
46 Geoffrey Hinton
47 Hermann Ney
48 Philip Yu
49 Shaogang Gong
50 Pieter Abbeel
51 Scott Shenker
52 B K
53 Sergey Levine
54 William Freeman
55 Robert Schapire
56 Zhi-Hua Zhou
57 Wen Gao
58 Antonio Torralba
59 Hans-Peter Seidel
60 Daniel Cremers
61 Raquel Urtasun
62 Luc Van
63 Qiang Yang
64 Qi Tian
65 A M
66 Roland Siegwart
67 Roberto Cipolla
68 Jiaya Jia
69 Kristen Grauman
70 Daphne Koller
71 Bernhard Scholkopf
72 Michael Jordan
73 Jack Dongarra
74 Alan Yuille
75 Laurens der
76 Li Fei-Fei
77 Peter Stone
78 Chunhua Shen
79 Shih-Fu Chang
80 A Tekalp
81 Dan Roth
82 Pietro Perona
83 Fredo Durand


In [0]:
print("Total: ", len(genders))

print(genders.count('female'))
print(genders.count('male'))
print(genders.count('unknown'))

Total:  455
46
402
7


### Purge delta tables

In [0]:
# JSON parts

for delta_table in dblpv13_delta_parts:
    dbutils.fs.rm("dbfs:{}".format(delta_table), True)
    print(delta_table, "deleted")


/user/hive/warehouse/dblpv13_edited_parsed_part_1 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_2 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_3 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_4 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_5 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_6 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_7 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_8 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_9 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_10 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_11 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_12 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_13 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_14 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_15 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_16 deleted
/user/hive/warehouse/dblpv13_edited_parsed_part_17 deleted
/user/

In [0]:
# dimensions

dbutils.fs.rm("dbfs:/user/hive/warehouse/dim_date", True)
dbutils.fs.rm("dbfs:/user/hive/warehouse/dim_doc_type", True)
dbutils.fs.rm("dbfs:/user/hive/warehouse/dim_publication", True)
dbutils.fs.rm("dbfs:/user/hive/warehouse/dim_venue", True)
dbutils.fs.rm("dbfs:/user/hive/warehouse/dim_fos_general", True)
dbutils.fs.rm("dbfs:/user/hive/warehouse/dim_fos_specific", True)
dbutils.fs.rm("dbfs:/user/hive/warehouse/dim_organization", True)
dbutils.fs.rm("dbfs:/user/hive/warehouse/dim_author", True)
dbutils.fs.rm("dbfs:/user/hive/warehouse/dim_language", True)

Out[12]: True

In [0]:
# fact table

dbutils.fs.rm("dbfs:/user/hive/warehouse/fact_dblp", True)


Out[13]: True

In [0]:
# extra

dbutils.fs.rm("dbfs:/user/hive/warehouse/df_hindex", True)

Out[30]: True

In [0]:
%sh

ls -lsh /mnt

total 32K
 24K -rw-r--r-- 1 root root  21K May 28 08:58 dictionary_fos.txt
4.0K drwxr-xr-x 2 root root 4.0K May 28 07:37 driver-daemon
4.0K drwxr-xr-x 2 root root 4.0K May 28 07:37 readonly


In [0]:
%fs

ls /user/hive/warehouse/

path name size modificationTime dbfs:/user/hive/warehouse/_committed_140098711880695482 _committed_140098711880695482 222 1653503414000 dbfs:/user/hive/warehouse/_committed_1823990921207546219 _committed_1823990921207546219 223 1653503026000 dbfs:/user/hive/warehouse/_committed_2618448479493195264 _committed_2618448479493195264 222 1653500590000 dbfs:/user/hive/warehouse/_committed_276202957567659857 _committed_276202957567659857 222 1653500378000 dbfs:/user/hive/warehouse/_committed_4560362115751107150 _committed_4560362115751107150 223 1653503230000 dbfs:/user/hive/warehouse/_committed_4781748796520471704 _committed_4781748796520471704 222 1653502480000 dbfs:/user/hive/warehouse/_committed_4945852690702862520 _committed_4945852690702862520 223 1653500814000 dbfs:/user/hive/warehouse/_committed_5454470160437766372 _committed_5454470160437766372 223 1653501036000 dbfs:/user/hive/warehouse/_committed_641909369749824286 _committed_641909369749824286 222 1653502199000 dbfs:/user/hive/warehouse/_committed_7206901163515394298 _committed_7206901163515394298 223 1653502861000 dbfs:/user/hive/warehouse/_committed_7494790486012769035 _committed_7494790486012769035 223 1653501763000 dbfs:/user/hive/warehouse/_committed_8842716102152835588 _committed_8842716102152835588 223 1653501974000 dbfs:/user/hive/warehouse/_committed_8961684560190982263 _committed_8961684560190982263 223 1653501251000 dbfs:/user/hive/warehouse/_committed_9047904734868132260 _committed_9047904734868132260 223 1653502693000 dbfs:/user/hive/warehouse/_committed_9191319528001579417 _committed_9191319528001579417 234 1653500187000 dbfs:/user/hive/warehouse/_started_140098711880695482 _started_140098711880695482 0 1653503380000 dbfs:/user/hive/warehouse/_started_1823990921207546219 _started_1823990921207546219 0 1653502980000 dbfs:/user/hive/warehouse/_started_4560362115751107150 _started_4560362115751107150 0 1653503193000 dbfs:/user/hive/warehouse/_started_4781748796520471704 _started_4781748796520471704 0 1653502421000 dbfs:/user/hive/warehouse/_started_641909369749824286 _started_641909369749824286 0 1653502158000 dbfs:/user/hive/warehouse/_started_7206901163515394298 _started_7206901163515394298 0 1653502832000 dbfs:/user/hive/warehouse/_started_7494790486012769035 _started_7494790486012769035 0 1653501744000 dbfs:/user/hive/warehouse/_started_8842716102152835588 _started_8842716102152835588 0 1653501915000 dbfs:/user/hive/warehouse/_started_9047904734868132260 _started_9047904734868132260 0 1653502665000 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_1/ dblpv13_edited_parsed_part_1/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_10/ dblpv13_edited_parsed_part_10/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_11/ dblpv13_edited_parsed_part_11/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_12/ dblpv13_edited_parsed_part_12/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_13/ dblpv13_edited_parsed_part_13/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_14/ dblpv13_edited_parsed_part_14/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_15/ dblpv13_edited_parsed_part_15/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_16/ dblpv13_edited_parsed_part_16/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_17/ dblpv13_edited_parsed_part_17/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_18/ dblpv13_edited_parsed_part_18/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_19/ dblpv13_edited_parsed_part_19/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_2/ dblpv13_edited_parsed_part_2/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_20/ dblpv13_edited_parsed_part_20/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_21/ dblpv13_edited_parsed_part_21/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_22/ dblpv13_edited_parsed_part_22/ 0 0 dbfs:/user/hive/warehouse/dblpv13_edited_parsed_part_3/ dblpv13_edited_parsed_part_3/ 0 0 dbfs:/user/hive/wareho